# Introduksjon til Spark
Apache Spark er et åpent kildekode rammeverk for distribuert databehandling av _store_ datamengder. Via grensesnittet til Spark, har man muligheten til å skrive programmer med implisitt data parallellisme med støtte for sanntidsanalyse og avanserte verktøy som maskinlæring.

![](https://files.training.databricks.com/images/sparkcluster.png)

#### Spark Sesjonen
**'Spark Sesjonen'** (_SparkSession_) er inngangspunktet til Spark for å jobbe med DataFrames og Dataset. Via den får man tilgang til Spark funksjonaliteter inkludert lesing av data, håndtering av konfigurasjoner og tilgang til den underliggende 'Spark Konteksten' (_SparkContext_).

I teorien kan man opprette så mange sesjoner som man ønsker, f.eks. om man ønsker at flere brukere skal kunne kjøre kode mot samme kluster.

I en Databricks notebook, vil **'Spark Sesjonen'** allerede være instansiert på forhånd.

_Sørg for at du har et cluster tilgjengelig, før du starter på notebooken her. For å fest en Databricks notebook til et cluster [se her.](https://docs.databricks.com/en/notebooks/notebook-ui.html#compute-resources-for-notebooks)_

**Spark Sesjon** er tilgjengelig i Databricks gjennom den globale notebook variabelen `spark`.

In [0]:
# Kjør denne cellen for å skrive ut Spark Sesjonen
spark

![](https://files.training.databricks.com/images/105/unified-engine.png)

Det er noen viktige grensesnitt man må kjenne til for å kunne bruke Spark. Spesielt med tanke på at Spark er et prosseserings verktøy for store datamengder.

#### Dataset
Dataset er den nyeste abstraksjonen av en distribuert kolleksjon av data, og kan sees på som en kombinasjon av DataFrames og RDDer. Det gir et typet grensesnitt som er tilgjengelig i RDDer, samtidig som det gir mye av den samme funksjonaliteten fra DataFrames. Dataset APIet er tilgjengelig i Scala og Java.
#### DataFrame
DataFrame er en samling av distribuerte Rad-typer. Disse gir et fleksibelt grensesnitt og er liknende i konsept til DataFrames, for de som er kjent med det gjennom Pandas (Python bibliotek) og R-språket. DataFrames APIet er tilgjengelig i Python.
#### RDD (Resilient Distributed Dataset)
Apache Spark's første abstraksjon av en distribuert kolleksjon av data var RDD. Det er et grensesnitt over en sekvens av dataobjekter som består av en eller flere typer som er distribuert utover et kluster av maskiner. Selv om dette er den opprinnelige datastrukturen som er tilgjengelig, bør nye brukere hovedsaklig fokusere på Dataset/DataFrame som eksponerer mye av funksjonaliteten til RDDer.


La oss bruke **Spark Sesjonen** til å lese inn en fil og opprette en DataFrame.

In [0]:
# Les inn en text fil
min_1_dataframe = spark.read.text("/databricks-datasets/learning-spark-v2/SPARK_README.md")

print(min_1_dataframe)

DataFrame[value: string]


Normalt ville man forventet at `print` faktisk skrev ut verdien til DataFramen over, men det er ikke det som skjer. Dette er fordi Spark tillater brukeren å gjøre 2 forskjellige operasjoner på en DataFrame, dette er det vi kaller for **transformasjoner** og **handlinger**.

#### Transformasjoner
Transformasjoner i Spark er late av natur, og de vil ikke bli utført før man på kaller en **handling**. Dette vil si at man kan bygge oppe en større transformasjons rekke, i en interaktiv notebook, over flere celler før en eneste transformasjon har skjedd på dataene. Noen vanlige transformasjoner i Spark inkluderer:
- `filter()`
- `select()`
- `groupBy()`
- `withColumn()`

#### Handlinger
Handlinger er operasjoner som utløser utførelsen av en Spark-jobb og returnerer et resultat. Jobben består av å kjøre alle de tidligere transformasjonene for å få tilbake et faktisk resultat. En handling er sammensatt av en eller flere jobber som består av oppgaver som vil bli utført av arbeiderne parallelt der det er mulig.
Noen vanlige handlinger i Spark inkluderer:
- `show()`
- `count()`
- `take()`
- `collect()`

![](https://files.training.databricks.com/images/wiki-book/pagecounts/trans_and_actions.png)




In [0]:
# En transformasjon
filtered = min_1_dataframe.filter(min_1_dataframe.value.contains("Spark"))

In [0]:
# To handlinger
print(min_1_dataframe.show(5))
print(filtered.show(5))

+--------------------+
|               value|
+--------------------+
|      # Apache Spark|
|                    |
|Spark is a fast a...|
|high-level APIs i...|
|supports general ...|
+--------------------+
only showing top 5 rows

None
+--------------------+
|               value|
+--------------------+
|      # Apache Spark|
|Spark is a fast a...|
|rich set of highe...|
|and Spark Streami...|
|You can find the ...|
+--------------------+
only showing top 5 rows

None


Databricks tilbyr en litt penere utskrifts funskjon, som heter `display`.

In [0]:
min_1_dataframe.display()
filtered.display()

value # Apache Spark Spark is a fast and general cluster computing system for Big Data. It provides high-level APIs in Scala, Java, Python, and R, and an optimized engine that supports general computation graphs for data analysis. It also supports a rich set of higher-level tools including Spark SQL for SQL and DataFrames, MLlib for machine learning, GraphX for graph processing, and Spark Streaming for stream processing. ## Online Documentation You can find the latest Spark documentation, including a programming guide, on the [project web page](http://spark.apache.org/documentation.html) and [project wiki](https://cwiki.apache.org/confluence/display/SPARK). This README file only contains basic setup instructions. ## Building Spark Spark is built using [Apache Maven](http://maven.apache.org/). To build Spark and its example programs, run: build/mvn -DskipTests clean package (You do not need to do this if you downloaded a pre-built package.) More detailed documentation is available from the project site, at ["Building Spark"](http://spark.apache.org/docs/latest/building-spark.html). ## Interactive Scala Shell The easiest way to start using Spark is through the Scala shell: ./bin/spark-shell Try the following command, which should return 1000: scala> sc.parallelize(1 to 1000).count() ## Interactive Python Shell Alternatively, if you prefer Python, you can use the Python shell: ./bin/pyspark And run the following command, which should also return 1000: >>> sc.parallelize(range(1000)).count() ## Example Programs Spark also comes with several sample programs in the `examples` directory. To run one of them, use `./bin/run-example [params]`. For example: ./bin/run-example SparkPi will run the Pi example locally. You can set the MASTER environment variable when running examples to submit examples to a cluster. This can be a mesos:// or spark:// URL, "yarn" to run on YARN, and "local" to run locally with one thread, or "local[N]" to run locally with N threads. You can also use an abbreviated class name if the class is in the `examples` package. For instance: MASTER=spark://host:7077 ./bin/run-example SparkPi Many of the example programs print usage help if no params are given. ## Running Tests Testing first requires [building Spark](#building-spark). Once Spark is built, tests can be run using: ./dev/run-tests Please see the guidance on how to [run tests for a module, or individual tests](https://cwiki.apache.org/confluence/display/SPARK/Useful+Developer+Tools). ## A Note About Hadoop Versions Spark uses the Hadoop core library to talk to HDFS and other Hadoop-supported storage systems. Because the protocols have changed in different versions of Hadoop, you must build Spark against the same version that your cluster runs. Please refer to the build documentation at ["Specifying the Hadoop Version"](http://spark.apache.org/docs/latest/building-spark.html#specifying-the-hadoop-version) for detailed guidance on building for a particular distribution of Hadoop, including building for particular Hive and Hive Thriftserver distributions. ## Configuration Please refer to the [Configuration Guide](http://spark.apache.org/docs/latest/configuration.html) in the online documentation for an overview on how to configure Spark.

value # Apache Spark Spark is a fast and general cluster computing system for Big Data. It provides rich set of higher-level tools including Spark SQL for SQL and DataFrames, and Spark Streaming for stream processing. You can find the latest Spark documentation, including a programming ## Building Spark Spark is built using [Apache Maven](http://maven.apache.org/). To build Spark and its example programs, run: ["Building Spark"](http://spark.apache.org/docs/latest/building-spark.html). The easiest way to start using Spark is through the Scala shell: Spark also comes with several sample programs in the `examples` directory. ./bin/run-example SparkPi MASTER=spark://host:7077 ./bin/run-example SparkPi Testing first requires [building Spark](#building-spark). Once Spark is built, tests Spark uses the Hadoop core library to talk to HDFS and other Hadoop-supported Hadoop, you must build Spark against the same version that your cluster runs. in the online documentation for an overview on how to configure Spark.


Hovedårsaken til at Spark består av handlinger og transformasjoner, er at dette gir en enkel måte å optimalisere hele beregningskjeden på. Fremfor å fokusere på de individuelle delene, prøver Spark å se helheten i jobben den blir gitt. Dette gjør Spark eksepsjonelt rask i visse komputeringer, da det kan utføre alle relevante komputasjoner i parallell. Teknisk sett, så "pipeliner" Spark denne beregningen, noe vi kan se i bildet nedenfor. Dette innebærer at visse beregninger kan utføres samtidig (`withColumn()`,`filter()`,`sum()`) fremfor å måtte utføre én operasjon for alle dataelementene, og deretter den neste operasjonen.

![transformasjoner og handlinger](https://files.training.databricks.com/images/eLearning/ucdavis/transformations-narrow.png)

Apache Spark kan også holde resultater i minnet, i motsetning til andre rammeverk som umiddelbart skriver til disk etter hver oppgave (Hadoop).

#### Arkitekturen til Apache Spark

La oss ta en rask titt på Apache Sparks arkitektur. Som nevnt tidligere, lar Apache Spark deg distribuere arbeidslasten din utover et nettverk av maskiner, og dette oppnås gjennom en **driver-arbeider** type arkitektur. Her er det en driver node i et kluster av maskiner, ledsaget av arbeider noder. Driveren sender arbeid til arbeiderene og instruerer dem om å hente data enten fra minnet eller fra disk (eller fra en annen datakilde som GCS eller PostGIS).

Diagrammet nedenfor viser et eksempel på et Apache Spark-kluster. I hovedsak finnes det en Driver-node som kommuniserer med executor-noder. Hver av disse executor-nodene har `slots` som logisk sett fungerer som cpu kjerne.

![spark-arkitektur](https://files.training.databricks.com/images/105/spark_cluster_slots.png)

Driveren sender oppgaver til de ledige `slots` på executorne når det er arbeid som må gjøres:

![spark-arkitektur](https://files.training.databricks.com/images/105/spark_cluster_tasks.png)

Du kan se detaljene i din Apache Spark-applikasjon i Apache Spark web UI. Web UI er tilgjengelig i Databricks ved å gå til "Clusters" og deretter klikke på "View Spark UI"-lenken for klusteret ditt. Det er også tilgjengelig ved å klikke øverst til høyre på denne notatboken der du velger klusteret som er koblet til denne notatboken.

På et høyt nivå består hver Apache Spark-applikasjon av et driverprogram som starter forskjellige parallelle operasjoner på arbeider-nodene, Java Virtual Machines (JVMs), som kjører enten i et kluster eller lokalt på samme maskin. I Databricks, er notebook grensesnittet driverprogrammet. Dette driverprogrammet oppretter distribuerte datasett på klusteret, og deretter utføres operasjoner (transformasjoner og handlinger) på disse datasettene. Driverprogrammet får tilgang til Apache Spark gjennom et Spark Sesjon-objekt.

#### Et Siste Eksempel

La oss sette sammen alle prinsippene vi har introdusert over og sette det i en kontekst ved å lese inn en fil, Gjøre noen transformasjoner med datasettet og til slutt avslutte med en handling.

Vi skal, med andre ord, bygge opp en plan for hvordan vi skal få tilgang til dataene, og deretter endelig utføre den planen med en handling. Vi går gjennom en prosess med å analysere forespørselen, bygger opp en plan, sammenligne dem og til slutt utfører vi den.

![Spark Query Plan](https://files.training.databricks.com/images/wiki-book/pageviews/catalyst.png)

Vi kommer ikke til å gå mer innpå den underliggende optimalisereren her, men man kan [lese mer her.](https://www.databricks.com/glossary/catalyst-optimizer)

La oss lese inn et av datasettene som databricks tilbyr.
- Formatet på filen er `csv`
- Filen inneholder overskrift på første raden
- `inferSchema` betyr at vi lar Spark automatisk oppdage datatypene til kolonnene
   - Kostnaden vi betaler for dette er at filen må leses mer enn en gang

In [0]:
path = "/databricks-datasets/Rdatasets/data-001/csv/ggplot2/diamonds.csv"

diamanter = spark.read.format("csv")\
  .option("header","true")\
  .option("inferSchema", "true")\
  .load(path)

Når vi har lest inn dataene, er vi klare til å kjøre noen komputasjoner. Men før vi kan utføre noen transformasjoner på datasettet, må vi vite hvordan dataene ser ut. Vi kan gjøre dette i form av en handling, enten ved hjelp av `show()` eller `display()`.

In [0]:
diamanter.display()

_c0 carat cut color clarity depth table price x y z 1 0.23 Ideal E SI2 61.5 55.0 326 3.95 3.98 2.43 2 0.21 Premium E SI1 59.8 61.0 326 3.89 3.84 2.31 3 0.23 Good E VS1 56.9 65.0 327 4.05 4.07 2.31 4 0.29 Premium I VS2 62.4 58.0 334 4.2 4.23 2.63 5 0.31 Good J SI2 63.3 58.0 335 4.34 4.35 2.75 6 0.24 Very Good J VVS2 62.8 57.0 336 3.94 3.96 2.48 7 0.24 Very Good I VVS1 62.3 57.0 336 3.95 3.98 2.47 8 0.26 Very Good H SI1 61.9 55.0 337 4.07 4.11 2.53 9 0.22 Fair E VS2 65.1 61.0 337 3.87 3.78 2.49 10 0.23 Very Good H VS1 59.4 61.0 338 4.0 4.05 2.39 11 0.3 Good J SI1 64.0 55.0 339 4.25 4.28 2.73 12 0.23 Ideal J VS1 62.8 56.0 340 3.93 3.9 2.46 13 0.22 Premium F SI1 60.4 61.0 342 3.88 3.84 2.33 14 0.31 Ideal J SI2 62.2 54.0 344 4.35 4.37 2.71 15 0.2 Premium E SI2 60.2 62.0 345 3.79 3.75 2.27 16 0.32 Premium E I1 60.9 58.0 345 4.38 4.42 2.68 17 0.3 Ideal I SI2 62.0 54.0 348 4.31 4.34 2.68 18 0.3 Good J SI1 63.4 54.0 351 4.23 4.29 2.7 19 0.3 Good J SI1 63.8 56.0 351 4.23 4.26 2.71 20 0.3 Very Good J SI1 62.7 59.0 351 4.21 4.27 2.66 21 0.3 Good I SI2 63.3 56.0 351 4.26 4.3 2.71 22 0.23 Very Good E VS2 63.8 55.0 352 3.85 3.92 2.48 23 0.23 Very Good H VS1 61.0 57.0 353 3.94 3.96 2.41 24 0.31 Very Good J SI1 59.4 62.0 353 4.39 4.43 2.62 25 0.31 Very Good J SI1 58.1 62.0 353 4.44 4.47 2.59 26 0.23 Very Good G VVS2 60.4 58.0 354 3.97 4.01 2.41 27 0.24 Premium I VS1 62.5 57.0 355 3.97 3.94 2.47 28 0.3 Very Good J VS2 62.2 57.0 357 4.28 4.3 2.67 29 0.23 Very Good D VS2 60.5 61.0 357 3.96 3.97 2.4 30 0.23 Very Good F VS1 60.9 57.0 357 3.96 3.99 2.42 31 0.23 Very Good F VS1 60.0 57.0 402 4.0 4.03 2.41 32 0.23 Very Good F VS1 59.8 57.0 402 4.04 4.06 2.42 33 0.23 Very Good E VS1 60.7 59.0 402 3.97 4.01 2.42 34 0.23 Very Good E VS1 59.5 58.0 402 4.01 4.06 2.4 35 0.23 Very Good D VS1 61.9 58.0 402 3.92 3.96 2.44 36 0.23 Good F VS1 58.2 59.0 402 4.06 4.08 2.37 37 0.23 Good E VS1 64.1 59.0 402 3.83 3.85 2.46 38 0.31 Good H SI1 64.0 54.0 402 4.29 4.31 2.75 39 0.26 Very Good D VS2 60.8 59.0 403 4.13 4.16 2.52 40 0.33 Ideal I SI2 61.8 55.0 403 4.49 4.51 2.78 41 0.33 Ideal I SI2 61.2 56.0 403 4.49 4.5 2.75 42 0.33 Ideal J SI1 61.1 56.0 403 4.49 4.55 2.76 43 0.26 Good D VS2 65.2 56.0 403 3.99 4.02 2.61 44 0.26 Good D VS1 58.4 63.0 403 4.19 4.24 2.46 45 0.32 Good H SI2 63.1 56.0 403 4.34 4.37 2.75 46 0.29 Premium F SI1 62.4 58.0 403 4.24 4.26 2.65 47 0.32 Very Good H SI2 61.8 55.0 403 4.35 4.42 2.71 48 0.32 Good H SI2 63.8 56.0 403 4.36 4.38 2.79 49 0.25 Very Good E VS2 63.3 60.0 404 4.0 4.03 2.54 50 0.29 Very Good H SI2 60.7 60.0 404 4.33 4.37 2.64 51 0.24 Very Good F SI1 60.9 61.0 404 4.02 4.03 2.45 52 0.23 Ideal G VS1 61.9 54.0 404 3.93 3.95 2.44 53 0.32 Ideal I SI1 60.9 55.0 404 4.45 4.48 2.72 54 0.22 Premium E VS2 61.6 58.0 404 3.93 3.89 2.41 55 0.22 Premium D VS2 59.3 62.0 404 3.91 3.88 2.31 56 0.3 Ideal I SI2 61.0 59.0 405 4.3 4.33 2.63 57 0.3 Premium J SI2 59.3 61.0 405 4.43 4.38 2.61 58 0.3 Very Good I SI1 62.6 57.0 405 4.25 4.28 2.67 59 0.3 Very Good I SI1 63.0 57.0 405 4.28 4.32 2.71 60 0.3 Good I SI1 63.2 55.0 405 4.25 4.29 2.7 61 0.35 Ideal I VS1 60.9 57.0 552 4.54 4.59 2.78 62 0.3 Premium D SI1 62.6 59.0 552 4.23 4.27 2.66 63 0.3 Ideal D SI1 62.5 57.0 552 4.29 4.32 2.69 64 0.3 Ideal D SI1 62.1 56.0 552 4.3 4.33 2.68 65 0.42 Premium I SI2 61.5 59.0 552 4.78 4.84 2.96 66 0.28 Ideal G VVS2 61.4 56.0 553 4.19 4.22 2.58 67 0.32 Ideal I VVS1 62.0 55.3 553 4.39 4.42 2.73 68 0.31 Very Good G SI1 63.3 57.0 553 4.33 4.3 2.73 69 0.31 Premium G SI1 61.8 58.0 553 4.35 4.32 2.68 70 0.24 Premium E VVS1 60.7 58.0 553 4.01 4.03 2.44 71 0.24 Very Good D VVS1 61.5 60.0 553 3.97 4.0 2.45 72 0.3 Very Good H SI1 63.1 56.0 554 4.29 4.27 2.7 73 0.3 Premium H SI1 62.9 59.0 554 4.28 4.24 2.68 74 0.3 Premium H SI1 62.5 57.0 554 4.29 4.25 2.67 75 0.3 Good H SI1 63.7 57.0 554 4.28 4.26 2.72 76 0.26 Very Good F VVS2 59.2 60.0 554 4.19 4.22 2.49 77 0.26 Very Good E VVS2 59.9 58.0 554 4.15 4.23 2.51 78 0.26 Very Good D VVS2 62.4 54.0 554 4.08 4.13 2.56 79 0.26 Very Good D VVS

Styrken til `display` er at vi raskt og enkelt, ved hjelp av noen klikk, kan lage visualisjoner for å lettere kunne forstå dataene. La oss lage et plot hvor vi kan sammenligne pris, color og cut. Ved å trykke på `+` ikonet på toppen av tabellen kan vi velge å legge til en visualisering fane. For å få frem dataene i visualisjonen må vi kjøre cellen på nytt.

In [0]:
diamanter.display()

_c0 carat cut color clarity depth table price x y z 1 0.23 Ideal E SI2 61.5 55.0 326 3.95 3.98 2.43 2 0.21 Premium E SI1 59.8 61.0 326 3.89 3.84 2.31 3 0.23 Good E VS1 56.9 65.0 327 4.05 4.07 2.31 4 0.29 Premium I VS2 62.4 58.0 334 4.2 4.23 2.63 5 0.31 Good J SI2 63.3 58.0 335 4.34 4.35 2.75 6 0.24 Very Good J VVS2 62.8 57.0 336 3.94 3.96 2.48 7 0.24 Very Good I VVS1 62.3 57.0 336 3.95 3.98 2.47 8 0.26 Very Good H SI1 61.9 55.0 337 4.07 4.11 2.53 9 0.22 Fair E VS2 65.1 61.0 337 3.87 3.78 2.49 10 0.23 Very Good H VS1 59.4 61.0 338 4.0 4.05 2.39 11 0.3 Good J SI1 64.0 55.0 339 4.25 4.28 2.73 12 0.23 Ideal J VS1 62.8 56.0 340 3.93 3.9 2.46 13 0.22 Premium F SI1 60.4 61.0 342 3.88 3.84 2.33 14 0.31 Ideal J SI2 62.2 54.0 344 4.35 4.37 2.71 15 0.2 Premium E SI2 60.2 62.0 345 3.79 3.75 2.27 16 0.32 Premium E I1 60.9 58.0 345 4.38 4.42 2.68 17 0.3 Ideal I SI2 62.0 54.0 348 4.31 4.34 2.68 18 0.3 Good J SI1 63.4 54.0 351 4.23 4.29 2.7 19 0.3 Good J SI1 63.8 56.0 351 4.23 4.26 2.71 20 0.3 Very Good J SI1 62.7 59.0 351 4.21 4.27 2.66 21 0.3 Good I SI2 63.3 56.0 351 4.26 4.3 2.71 22 0.23 Very Good E VS2 63.8 55.0 352 3.85 3.92 2.48 23 0.23 Very Good H VS1 61.0 57.0 353 3.94 3.96 2.41 24 0.31 Very Good J SI1 59.4 62.0 353 4.39 4.43 2.62 25 0.31 Very Good J SI1 58.1 62.0 353 4.44 4.47 2.59 26 0.23 Very Good G VVS2 60.4 58.0 354 3.97 4.01 2.41 27 0.24 Premium I VS1 62.5 57.0 355 3.97 3.94 2.47 28 0.3 Very Good J VS2 62.2 57.0 357 4.28 4.3 2.67 29 0.23 Very Good D VS2 60.5 61.0 357 3.96 3.97 2.4 30 0.23 Very Good F VS1 60.9 57.0 357 3.96 3.99 2.42 31 0.23 Very Good F VS1 60.0 57.0 402 4.0 4.03 2.41 32 0.23 Very Good F VS1 59.8 57.0 402 4.04 4.06 2.42 33 0.23 Very Good E VS1 60.7 59.0 402 3.97 4.01 2.42 34 0.23 Very Good E VS1 59.5 58.0 402 4.01 4.06 2.4 35 0.23 Very Good D VS1 61.9 58.0 402 3.92 3.96 2.44 36 0.23 Good F VS1 58.2 59.0 402 4.06 4.08 2.37 37 0.23 Good E VS1 64.1 59.0 402 3.83 3.85 2.46 38 0.31 Good H SI1 64.0 54.0 402 4.29 4.31 2.75 39 0.26 Very Good D VS2 60.8 59.0 403 4.13 4.16 2.52 40 0.33 Ideal I SI2 61.8 55.0 403 4.49 4.51 2.78 41 0.33 Ideal I SI2 61.2 56.0 403 4.49 4.5 2.75 42 0.33 Ideal J SI1 61.1 56.0 403 4.49 4.55 2.76 43 0.26 Good D VS2 65.2 56.0 403 3.99 4.02 2.61 44 0.26 Good D VS1 58.4 63.0 403 4.19 4.24 2.46 45 0.32 Good H SI2 63.1 56.0 403 4.34 4.37 2.75 46 0.29 Premium F SI1 62.4 58.0 403 4.24 4.26 2.65 47 0.32 Very Good H SI2 61.8 55.0 403 4.35 4.42 2.71 48 0.32 Good H SI2 63.8 56.0 403 4.36 4.38 2.79 49 0.25 Very Good E VS2 63.3 60.0 404 4.0 4.03 2.54 50 0.29 Very Good H SI2 60.7 60.0 404 4.33 4.37 2.64 51 0.24 Very Good F SI1 60.9 61.0 404 4.02 4.03 2.45 52 0.23 Ideal G VS1 61.9 54.0 404 3.93 3.95 2.44 53 0.32 Ideal I SI1 60.9 55.0 404 4.45 4.48 2.72 54 0.22 Premium E VS2 61.6 58.0 404 3.93 3.89 2.41 55 0.22 Premium D VS2 59.3 62.0 404 3.91 3.88 2.31 56 0.3 Ideal I SI2 61.0 59.0 405 4.3 4.33 2.63 57 0.3 Premium J SI2 59.3 61.0 405 4.43 4.38 2.61 58 0.3 Very Good I SI1 62.6 57.0 405 4.25 4.28 2.67 59 0.3 Very Good I SI1 63.0 57.0 405 4.28 4.32 2.71 60 0.3 Good I SI1 63.2 55.0 405 4.25 4.29 2.7 61 0.35 Ideal I VS1 60.9 57.0 552 4.54 4.59 2.78 62 0.3 Premium D SI1 62.6 59.0 552 4.23 4.27 2.66 63 0.3 Ideal D SI1 62.5 57.0 552 4.29 4.32 2.69 64 0.3 Ideal D SI1 62.1 56.0 552 4.3 4.33 2.68 65 0.42 Premium I SI2 61.5 59.0 552 4.78 4.84 2.96 66 0.28 Ideal G VVS2 61.4 56.0 553 4.19 4.22 2.58 67 0.32 Ideal I VVS1 62.0 55.3 553 4.39 4.42 2.73 68 0.31 Very Good G SI1 63.3 57.0 553 4.33 4.3 2.73 69 0.31 Premium G SI1 61.8 58.0 553 4.35 4.32 2.68 70 0.24 Premium E VVS1 60.7 58.0 553 4.01 4.03 2.44 71 0.24 Very Good D VVS1 61.5 60.0 553 3.97 4.0 2.45 72 0.3 Very Good H SI1 63.1 56.0 554 4.29 4.27 2.7 73 0.3 Premium H SI1 62.9 59.0 554 4.28 4.24 2.68 74 0.3 Premium H SI1 62.5 57.0 554 4.29 4.25 2.67 75 0.3 Good H SI1 63.7 57.0 554 4.28 4.26 2.72 76 0.26 Very Good F VVS2 59.2 60.0 554 4.19 4.22 2.49 77 0.26 Very Good E VVS2 59.9 58.0 554 4.15 4.23 2.51 78 0.26 Very Good D VVS2 62.4 54.0 554 4.08 4.13 2.56 79 0.26 Very Good D VVS

Databricks visualization. Run in Databricks to view.

La oss gjøre noen enkle transformasjoner på datasettet, før vi analyserer den midlertidige planen Spark har for å påføre disse transformasjon på dataene.

Vi skal gjøre noen veldig enkle transformasjoner, først grupperer vi dataene på to variabler, cut og color, før vi beregner gjennomsnittsprisen basert på disse to variablene. Etter dette ønsker vi å slå sammen det nye datasettet med det originale datasettet på kolonnen color, og velge carat og gjennomsnittsprisen.

In [0]:
gruppert_data = diamanter.groupBy("cut", "color").avg("price")

joined_data = gruppert_data\
  .join(diamanter, on='color', how='inner')\
  .select("`avg(price)`", "carat")

Disse transformasjonene er nå på en måte fullført, men ingenting har skjedd. Som du ser ovenfor, har ikke Spark retunert et resultat tilbake!

Grunnen til det er at disse beregningene er late av natur. Dette er en intelligent optimalisering som muliggjør at enhver beregning kan bli rekalkulert fra kildedataene, noe som gjør at Apache Spark kan håndtere eventuelle feil som oppstår underveis, og håndtere forsinkelser på en vellykket måte. For det andre, kan Apache Spark optimalisere beregningen slik at transformasjonen på dataene kan utføres mer effektivt, ved å lage en plan for hvordan dette arbeidet vil utføres. Dette vil ikke si at man slipper å tenke på hvilken transformasjoner som bør komme før andre transformasjoner. Mer om dette senere.

For å få en følelse av hva denne planen består av, kan vi bruke explain-metoden. Husk at ingen av beregningene våre har blitt utført ennå, så alt denne explain-metoden gjør er å fortelle oss hvordan du beregner dette eksakte datasettet.

In [0]:
joined_data.explain()

== Physical Plan ==
AdaptiveSparkPlan isFinalPlan=true
+- == Final Plan ==
   ResultQueryStage 2, Statistics(sizeInBytes=63.1 MiB, ColumnStat: N/A, isRuntime=true)
   +- *(3) Project [avg(price)#422, carat#428]
      +- *(3) BroadcastHashJoin [color#52], [color#430], Inner, BuildLeft, false
         :- ShuffleQueryStage 1, Statistics(sizeInBytes=1120.0 B, rowCount=35, ColumnStat: N/A, isRuntime=true)
         :  +- Exchange SinglePartition, EXECUTOR_BROADCAST, [plan_id=217]
         :     +- *(2) HashAggregate(keys=[cut#51, color#52], functions=[finalmerge_avg(merge sum#456, count#457L) AS avg(price#56)#421])
         :        +- AQEShuffleRead coalesced
         :           +- ShuffleQueryStage 0, Statistics(sizeInBytes=2016.0 B, rowCount=35, ColumnStat: N/A, isRuntime=true)
         :              +- Exchange hashpartitioning(cut#51, color#52, 200), ENSURE_REQUIREMENTS, [plan_id=182]
         :                 +- *(1) HashAggregate(keys=[cut#51, color#52], functions=[partial_avg(pric

Prøv å se om du forstår noe av planen over. Vi skal ikke gå noe dypere inn på dette her, men for mer [info se her.](https://docs.databricks.com/en/optimizations/cbo.html)

In [0]:
joined_data.count()

269700

Vi kan undersøke hvilken plan Spark brukte under eksekveringen av jobben ved å trykke på pilen ved siden av `(4) Spark Jobs` på bunnen av cellen over.
Etter at jobben har fått kjørt ferdig, kan vi trykke på `View` linken, etterfulgt av `DAG Visualization` knappen. Dette gir oss direkte tilgang til Spark UIen fra notebooken våres.

Dette er den Direkte Asykliske Grafen (DAG) av alle beregningene vi nettopp har kjørt. Dette blir ofte kalt for datalineage, da det gir oss en oversikt over hva som har skjedd med dataene fra vi leste de inn til vi har prosessert de ferdig.

Det er takket være de late transformasjonen at denne DAGen kan bli generert. Under genereringen av stegene som inngår i DAGen, optimaliserer Spark en del ting underveis. Dette er en av hovedgrunnen til å bruke DataFrame og Dataset i stedet for RDD APIet. Du vil se eksempler på `WholeStageCodeGen` og `tungsten` i planene, og disse er en del av forbedringene i Spark SQL, [som du kan lese mer om på Databricks sine sider.](https://www.databricks.com/glossary/tungsten)

#### Caching

Caching er en viktig funksjon i Apache Spark som lar deg lagre data i minnet under beregninger. Dette kan bidra til å øke hastigheten på tilgangen til ofte brukte tabeller eller datastykker. Caching er spesielt nyttig for iterative algoritmer som arbeider gjentatte ganger med de samme dataene. Men det er viktig å merke seg at caching ikke er en universalløsning for alle hastighetsproblemer. Andre viktige konsepter som data-partisjonering, data-klustering og bøttefordeling kan ha en mye større effekt på utførelsen av jobben din enn caching. Husk imidlertid at disse er alle verktøy i verktøykassen din!

For å cache en DataFrame eller RDD, kan du enkelt bruke `cache`-funksjonen

In [0]:
joined_data.cache()

DataFrame[avg(price): double, carat: double]

Caching, som en transformasjon, utføres lat. Det betyr at dataene ikke blir lagret i minnet før du kaller en handling (action) på datasettet.

Vi har fortalt Apache Spark at den skal `cache` datasettet vårt etter at vi har utført en handling. La oss påføre en handling på dataene med en `count` to ganger. Første gang vil dette opprette datasettet, cache den i minnet og deretter returnere resultatet. Andre gang, i stedet for å beregne hele datasettet på nytt, vil den bare hente versjonen som allerede er i minnet.

In [0]:
joined_data.count()

269700

In [0]:
joined_data.count()

269700

Som vi kan se, utføres `count` nummer to flere ganger raskere enn count nummer en.

For å se om en DataFrame er cachet kan vi kjøre følgende celle.

In [0]:
print(joined_data.storageLevel.useMemory)

True


Vi kan printe antall parisjoner datasettet har. For å kunne gjøre det må vi hente informasjon fra det underliggende Resiliant Distributed Dataset (RDD).

In [0]:
print(f"DataFrame består av {joined_data.rdd.getNumPartitions()} partisjoner")

DataFrame består av 1 partisjoner


Man får ikke helt de store parallelle operasjonen på dette datasettet.